In [107]:
from docplex.mp.model import Model
import pandas as pd
import numpy as np
np.seterr(all="ignore")
import math
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import warnings
warnings.filterwarnings('ignore')

def euclid_dist (x1, y1, x2, y2):
    return math.sqrt((x1-x2)**2 + (y1-y2)**2)

#input data from .csv file
wh_coords = pd.read_csv("./coordinates_old.csv")
x_coord=wh_coords['x'].values
y_coord=wh_coords['y'].values
product_data=pd.read_csv("./product_data.csv", index_col=0)
Q=product_data['TOT_MP'].values
W=product_data['VOL_DEPLETING'].values
#MP=product_data['MP'].values 
VOL = product_data['VOL'].values
LC = product_data['#LC'].values
dis = []
for i in range(len(wh_coords)):
    dis.append(euclid_dist(300,15,x_coord[i],y_coord[i]))

#Input data from context
Class=3 
L=len(dis)
P=len(product_data)
C = 3.5 #Slot max capacity
Z = 10
Zone_1=range(1,12)
Zone_2=range(13,49)
Zone_3=range(50,172)
Zone_4=range(173,208)
Zone_5=range(209,347)
Zone_6=range(348,359)
Zone_7=range(360,400)
Zone_8=range(401,679)
Zone_9=range(680,777)
Zone_10=range(778,827)
Stock_Zones=[Zone_1, Zone_2, Zone_3, Zone_4, Zone_5, Zone_6, Zone_7, Zone_8, Zone_9, Zone_10]

#Apc Matrix
A=np.zeros((P,Class),int) 

product_data['Class']='C' 
for i in range(len(product_data)):
    if W[i]>=15: 
        product_data['Class'][i] ='A' 
        A[[i],0] = 1 
    elif W[i]>=5 and W[i]<15:
        product_data['Class'][i]='B'
        A[[i],1]=1 
    else:
        product_data['Class'][i]='C'
        A[[i],2]=1 

restricted = []
for i in range(len(product_data)):
    if product_data['Class'][i] =='A': 
        restricted.append(i)

mdl = Model(name= 'WH_REVAMP') 

# Decision Variables
x = mdl.binary_var_matrix(L, P, name='X')  # 1 if product p is assigned to slot l, 0 otherwise
y = mdl.integer_var_matrix(L, P, name='Y')  # Number of LC of product p in slot l

#CONSTRAINTS:

# 1. At most one product type per location
for l in range(L):
    mdl.add_constraint(
        mdl.sum(x[l,p] for p in range(P)) <= 1
    )

# 2. Slot capacity
for p in range(P):
    for l in range(L):
        if math.isnan(VOL[p]):
            print(f"Warning: VOL[{p}] is NaN. Check your input data.")
        if math.isnan(C):
            print(f"Warning: C is NaN. Check your capacity value.")
        mdl.add_constraint(
            VOL[p]*y[l,p]<=C*x[l,p]
        )

# 3. Total LCs allocation
for p in range(P):
    mdl.add_constraint(
        mdl.sum(y[l,p] for l in range(L)) == LC[p]
    )

# OBJ FUNCTION
mdl.minimize(
    mdl.sum(dis[l]*x[l, p]*(3*A[p, 0] + 2*A[p, 1] + 1*A[p, 2]) for p in range(P) for l in range(L))
)

#print the implementation and solution of the objective function and the constraints
print(mdl.export_to_string())

# Set CPLEX parameters for detailed logging
mdl.parameters.mip.display = 2  # Display every node and integer solution
mdl.parameters.parallel = -1 # opportunistic
mdl.parameters.workmem = 16000 # 16 GB 

# warmstart=mdl.new_solution()
# warmstart.add_var_value(x,1)
# mdl.add_mip_start(warmstart)
sol=mdl.solve(log_output=True, clean_before_solve=True)
sol.display()

#save the solution in a list
x_list = []
for l in range(L):
    tmp = False
    for p in range(P):
        if sol.get_value(x[l, p]) == 1:
            tmp = True 
            x_list.append([l+1, p+1])
    if not tmp:
        x_list.append([l+1, -1])

print(x_list)

# 1. Write slot IDs to product_data(output).csv
product_data['Slot_IDs'] = ""  # Initialize an empty column for slot IDs
for l in range(L):
    for p in range(P):
        if sol.get_value(x[l, p]) == 1:
            product_data['Slot_IDs'][p] += f"{l+1}, "  # Add slot ID to the corresponding product row
product_data['Slot_IDs'] = product_data['Slot_IDs'].str.rstrip(', ')  # Remove trailing comma and space

#save data frame product_data into a .csv
product_data.to_csv("./products_data(output).csv", index=True, header=True)

# 2. Create an array with product ID, slot ID, and #LC
product_allocation = []
for l in range(L):
    for p in range(P):
        if sol.get_value(x[l, p]) == 1:
            product_allocation.append([p+1, l+1, int(sol.get_value(y[l, p]))])

def sort_by_product_id_and_slot_id(allocation):
    return (allocation[0], allocation[1])

a_class_products = []
for allocation in product_allocation:
    p_id = allocation[0]
    if product_data['Class'][p_id-1] == 'A':
        a_class_products.append(allocation)

# Sort A class products by product ID and then slot ID
a_class_products.sort(key=sort_by_product_id_and_slot_id)

# Extract slot IDs (second column)
slot_ids = [allocation[1] for allocation in a_class_products]

# Sort slot IDs
slot_ids.sort()

# Create a dictionary mapping original slot IDs to sorted slot IDs
slot_mapping = dict(zip([allocation[1] for allocation in a_class_products], slot_ids))

# Reassign sorted slot IDs back to the array
for i in range(len(a_class_products)):
    a_class_products[i][1] = slot_mapping[a_class_products[i][1]]

for i in range(len(a_class_products)):
    # Swap the first two columns (PRODUCT ID and SLOT ID)
    a_class_products[i][0], a_class_products[i][1] = a_class_products[i][1], a_class_products[i][0]
    # Replace the third column (#LC) with the product CLASS
    a_class_products[i][2] = product_data['Class'][a_class_products[i][1]-1]  # Access CLASS using the PRODUCT ID

print(a_class_products)

# Visualization
fig = go.Figure()

# Add empty slots first
empty_slots = [l for l, p in x_list if p == -1]
empty_x = x_coord[np.array(empty_slots)-1]
empty_y = y_coord[np.array(empty_slots)-1]
empty_text = [f"Slot: {l}<br>Empty" for l in empty_slots]  # Corrected

fig.add_trace(go.Scatter(
    x=empty_x,
    y=empty_y,
    mode='markers',
    marker=dict(color='green', size=10),
    text=empty_text,
    hoverinfo='text',
    name='Vuoto'
))

# Add slots for each product class with corresponding colors
for product_class, color in zip(['A', 'B', 'C'], ['blue', 'yellow', 'purple']):
    if product_class == 'A':  # Use a_class_products for class A
        occupied_slots = a_class_products
    else:
        occupied_slots = [[l, p, product_data['Class'][p-1]] for l, p in x_list if p != -1 and product_data['Class'][p-1] == product_class]

    occupied_x = x_coord[np.array([slot[0] for slot in occupied_slots])-1]  # Extract slot IDs from occupied_slots
    occupied_y = y_coord[np.array([slot[0] for slot in occupied_slots])-1]

    # Include product type index in hover text
    occupied_text = [
        f"Slot: {slot[0]}<br>Class: {slot[2]}<br>Product Index: {slot[1]}"  # Access CLASS directly from occupied_slots
        for slot in occupied_slots
    ]

    fig.add_trace(go.Scatter(
        x=occupied_x,
        y=occupied_y,
        mode='markers',
        marker=dict(color=color, size=10),
        text=occupied_text,
        hoverinfo='text',
        name=f'Classe {product_class}'
    ))
# Update layout
fig.update_layout(
    title='MCV WH OPTIMIZATION',
    xaxis_title='X',
    yaxis_title='Y',
    hovermode='closest',
    showlegend=True
)

fig.show()

\ This file has been generated by DOcplex
\ ENCODING=ISO-8859-1
\Problem name: WH_REVAMP

Minimize
 obj: 28.793174972552 X_0_0 + 28.793174972552 X_0_1 + 28.793174972552 X_0_2
      + 19.195449981701 X_0_3 + 28.793174972552 X_0_4 + 19.195449981701 X_0_5
      + 28.793174972552 X_0_6 + 19.195449981701 X_0_7 + 9.597724990851 X_0_8
      + 9.597724990851 X_0_9 + 9.597724990851 X_0_10 + 9.597724990851 X_0_11
      + 19.195449981701 X_0_12 + 28.793174972552 X_0_13 + 28.793174972552 X_0_14
      + 19.195449981701 X_0_15 + 19.195449981701 X_0_16 + 19.195449981701 X_0_17
      + 28.793174972552 X_0_18 + 19.195449981701 X_0_19 + 9.597724990851 X_0_20
      + 9.597724990851 X_0_21 + 19.195449981701 X_0_22 + 19.195449981701 X_0_23
      + 9.597724990851 X_0_24 + 9.597724990851 X_0_25 + 19.195449981701 X_0_26
      + 9.597724990851 X_0_27 + 9.597724990851 X_0_28 + 9.597724990851 X_0_29
      + 9.597724990851 X_0_30 + 19.195449981701 X_0_31 + 9.597724990851 X_0_32
      + 9.597724990851 X_0_33 + 9.5